# Implémentation du jeu de Nim

In [12]:
etat_jeu = [3, 4, 5] # Trois tas contenant respectivement 3, 4 et 5 objets.


### Exercice 1 

In [13]:
# A.
def afficher_etat(etat_jeu) :
    print(etat_jeu)


# B.
test1 = [3, 4, 5]
test2 = [0, 0, 0]
test3 = [1, 0, 2]

afficher_etat(test1)
afficher_etat(test2)
afficher_etat(test3)


[3, 4, 5]
[0, 0, 0]
[1, 0, 2]


### Exercice 2 : 

In [14]:
# A.

def generer_mouvement(etat_jeu) : 
    mouvements = []
    for i in range(len(etat_jeu)) : # On parcourt les tas
        for j in range(etat_jeu[i]) : # On tire le nombre d'objets dans le tas
            if etat_jeu[i] > 0 :
                mouvements.append((i, j+1)) # On ajoute le mouvement à la liste
    return mouvements

# B.
print(generer_mouvement(test1))
print(generer_mouvement(test2))
print(generer_mouvement(test3))

[(0, 1), (0, 2), (0, 3), (1, 1), (1, 2), (1, 3), (1, 4), (2, 1), (2, 2), (2, 3), (2, 4), (2, 5)]
[]
[(0, 1), (2, 1), (2, 2)]


### Exercice 3 : 

In [15]:
# A et B
def appliquer_mouvement(etat_jeu, tas_index, nombre_objets) :
    if nombre_objets > etat_jeu[tas_index] :
        print("Erreur : nombre d'objets à retirer supérieur au nombre d'objets dans le tas.")
        return etat_jeu
    else : 
        etat_jeu[tas_index] -= nombre_objets
        return etat_jeu




### Exercice 4 :

In [16]:
# A.
'''
def heuristique(etat_jeu) :
    return sum(etat_jeu)

print(heuristique(test1))
print(heuristique(test2))
print(heuristique(test3))'''

# B.
''' étant donné que  heuristique est égale à la somme des objets dans les tas, 
c'est donc un calcul simple qui ne dépend pas de l'ordre des tas. '''


" étant donné que  heuristique est égale à la somme des objets dans les tas, \nc'est donc un calcul simple qui ne dépend pas de l'ordre des tas. "

### Exercice 5 :

In [17]:
# A.
def est_etat_final(etat_jeu) :
    return sum(etat_jeu) == 0

# B.
def cout_transition(etat_courant, etat_suivant):
    return 1

# Exemple d'utilisation
etat_courant = [3, 4, 5]
etat_suivant = appliquer_mouvement(etat_courant, 0, 1)  # Devrait retourner [2, 4, 5]
print(cout_transition(etat_courant, etat_suivant))  # Devrait retourner 1

1


### Exercice 6 : 

In [18]:
import heapq

class Noeud:
    def __init__(self, etat, parent, cout, heuristique):
        self.etat = etat
        self.parent = parent
        self.cout = cout
        self.heuristique = heuristique

    def __lt__(self, other):
        return self.cout + self.heuristique < other.cout + other.heuristique

    def __eq__(self, other):
        return self.etat == other.etat

    def __hash__(self):
        return hash(tuple(self.etat))

    def __str__(self):
        return str(self.etat)
    
def xor_etat(etat_jeu):
    xor_total = 0
    for nb_objets in etat_jeu:
        xor_total ^= nb_objets
    return xor_total

def heuristique(etat_jeu):
    xor_valeur = xor_etat(etat_jeu)
    if xor_valeur == 0:
        # Position désavantageuse (perdante)
        return 100 + sum(etat_jeu)  # Pénalité
    else:
        # Position avantageuse (gagnante)
        return sum(etat_jeu)  # Heuristique standard

def est_etat_final(etat):
    return all(pile == 0 for pile in etat)

def generer_successeurs(etat):
    successeurs = []
    for i in range(len(etat)):
        if etat[i] > 0:
            for j in range(1, etat[i] + 1):
                nouvel_etat = etat[:]
                nouvel_etat[i] -= j
                successeurs.append(nouvel_etat)
    return successeurs

def algorithme_a_star(etat_initial):
    noeud_initial = Noeud(etat_initial, None, 0, heuristique(etat_initial))
    frontiere = []
    heapq.heappush(frontiere, noeud_initial)
    visites = set()

    while frontiere:
        noeud_courant = heapq.heappop(frontiere)

        if est_etat_final(noeud_courant.etat):
            chemin = []
            while noeud_courant:
                chemin.append(noeud_courant.etat)
                noeud_courant = noeud_courant.parent
            return chemin[::-1]

        visites.add(tuple(noeud_courant.etat))

        for successeur in generer_successeurs(noeud_courant.etat):
            if tuple(successeur) not in visites:
                cout = noeud_courant.cout + cout_transition(noeud_courant.etat, successeur)
                heur = heuristique(successeur)
                noeud_successeur = Noeud(successeur, noeud_courant, cout, heur)
                heapq.heappush(frontiere, noeud_successeur)

    return None

# Exemple d'utilisation
etat_initial = [4, 8, 5]
chemin_optimal = algorithme_a_star(etat_initial)
print(chemin_optimal)

[[4, 8, 5], [4, 0, 5], [0, 0, 5], [0, 0, 0]]


### Exercice 7 :

(voir cellule précédante)

A. 
- Initialisation:
    - Crée un nœud initial avec l'état initial du jeu.
    - Utilise une file de priorité (heap) pour gérer les nœuds à explorer.
    - Utilise un ensemble (set) pour stocker les états déjà visités.
- Boucle principale:
    - Tant que la file de priorité n'est pas vide, extraire le nœud avec le coût total (coût + heuristique) le plus bas.
    - Si l'état du nœud courant est un état final, reconstruire et retourner le chemin depuis l'état initial jusqu'à l'état final.
    - Ajouter l'état courant à l'ensemble des états visités.
    - Générer les états successeurs et les ajouter à la file de priorité s'ils n'ont pas été visités.
- Retour: Si aucun chemin n'est trouvé, retourner None.

B.
- Vérification des états visités, avant d'ajouter un successeur à la file de priorité, on vérifie si ils ont été visité.
- Une fois qu'un successeur est ajouté, il est ajouté à la file de priorité et marqué comme visité.


### Exercice 8 : 

A. 
Une représentation de son parent est crée dans la classe noeud. Lorsque qu'un successeur est crée, le noeud courant est défini comme parent


In [19]:
# B.

def reconstruire_chemin(noeud_final):
    """
    Reconstruit la séquence de mouvements depuis l’état initial jusqu’à l’état final.
    
    :param noeud_final: Le nœud final de l'algorithme A*.
    :return: Une liste des états représentant le chemin de l'état initial à l'état final.
    """
    chemin = []
    noeud_courant = noeud_final
    while noeud_courant:
        chemin.append(noeud_courant.etat)
        noeud_courant = noeud_courant.parent
    return chemin[::-1]

# Création d'un chemin d'exemple pour tester la fonction
etat_initial = [3, 4, 5]
etat_intermediaire = [3, 4, 4]
etat_final = [3, 4, 0]

noeud_final = Noeud(etat_final, Noeud(etat_intermediaire, Noeud(etat_initial, None, 0, 0), 1, 0), 2, 0)
chemin = reconstruire_chemin(noeud_final)
print(chemin)  # Devrait retourner [[3, 4, 5], [3, 4, 4], [3, 4, 0]]


[[3, 4, 5], [3, 4, 4], [3, 4, 0]]


### Exercice 9 : 

In [22]:
def jeu_nim(etat_initial):
    etat = etat_initial[:]
    while not est_etat_final(etat):
        afficher_etat(etat)
        try:
            pile = int(input("Entrez le numéro de la pile (1, 2, 3, ...): ")) - 1
            nb_objets = int(input("Entrez le nombre d'objets à retirer: "))
            appliquer_mouvement(etat, pile, nb_objets)
            afficher_etat(etat)
        except ValueError:
            print("Entrée invalide. Veuillez entrer des nombres entiers.")
            continue

        if est_etat_final(etat):
            print("\nFélicitations ! Vous avez gagné !")
            break

        # Tour de l'IA
        chemin_optimal = algorithme_a_star(etat)
        if chemin_optimal and len(chemin_optimal) > 1:
            etat_ia = chemin_optimal[1]
            print("\nL'IA joue...")
            etat = etat_ia

        if est_etat_final(etat):
            print("\n L'IA a gagné !")
            break

# Exemple d'utilisation
etat_initial = [3, 4, 5]
jeu_nim(etat_initial)

[3, 4, 5]
[3, 4, 5]

L'IA joue...
[3, 4, 0]
[0, 4, 0]

L'IA joue...

 L'IA a gagné !


### Exercice 10 :

In [21]:
def xor_etat(etat_jeu):
    xor_total = 0
    for nb_objets in etat_jeu:
        xor_total ^= nb_objets
    return xor_total

def heuristique_amelioree(etat_jeu):
    xor_valeur = xor_etat(etat_jeu)
    if xor_valeur == 0:
        # Position désavantageuse (perdante)
        return 100 + sum(etat_jeu)  # Pénalité
    else:
        # Position avantageuse (gagnante)
        return sum(etat_jeu)  # Heuristique standard

### Bonus

In [ ]:
# création d'un système de sauvegarde des parties jouées

def sauvegarder_partie(historique):
    """
    Sauvegarde l'historique de la partie dans un fichier.
    
    :param historique: Liste des coups effectués pendant la partie.
    :param fichier: Nom du fichier où sauvegarder l'historique.
    """
    fichier = "historique.txt"
    with open(fichier, "a") as f:
        f.write("Nouvelle partie :")
        for coup in historique:
            f.write(f"{coup} ")
        f.write("\n")


# modification de la fonction jeu_nim pour sauvegarder l'historique des coups
def jeu_nim(etat_initial):
    etat = etat_initial[:]
    historique = []
    while not est_etat_final(etat):
        afficher_etat(etat)
        try:
            pile = int(input("Entrez le numéro de la pile (1, 2, 3, ...): ")) - 1
            nb_objets = int(input("Entrez le nombre d'objets à retirer: "))
            historique.append(f"Joueur: Pile {pile + 1}, Objets retirés: {nb_objets}")
            appliquer_mouvement(etat, pile, nb_objets)
            historique.append(f"Player: {etat}")
            afficher_etat(etat)
        except ValueError:
            print("Entrée invalide. Veuillez entrer des nombres entiers.")
            continue

        if est_etat_final(etat):
            print("\nFélicitations ! Vous avez gagné !")
            break

        # Tour de l'IA
        chemin_optimal = algorithme_a_star(etat)
        if chemin_optimal and len(chemin_optimal) > 1:
            etat_ia = chemin_optimal[1]
            historique.append(f"IA: Pile {pile + 1}, Objets retirés: {nb_objets}")
            print("\nL'IA joue...")
            etat = etat_ia
            historique.append(f"AI: {etat}")

        if est_etat_final(etat):
            print("\n L'IA a gagné !")
            break
    sauvegarder_partie(historique)